## Import

In [ ]:
# !pip install -U git+https://github.com/qubvel-org/segmentation_models.pytorch

In [ ]:
from tqdm.notebook import tqdm, trange
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.optim import lr_scheduler
# import torch.utils.data as data
# import torchvision.transforms as transforms
import torchvision.models as models
from torchvision.transforms import v2
# import torch.nn.functional as F

# import optuna
# from optuna.trial import TrialState

import matplotlib.pyplot as plt
from gc import collect
import pandas as pd

import os
import cv2
from PIL import Image
# import seaborn as sns
# #---------------------------------------
# from sklearn.model_selection import train_test_split
# from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
#---------------------------------------
# import warnings
# warnings.filterwarnings("ignore")
# from gc import collect
# from joblib import Parallel, delayed
# from sklearn.preprocessing import LabelEncoder
# from keras.utils import to_categorical
# from numpy import savetxt
# from numpy import genfromtxt

from google.colab import drive
drive.mount('/content/drive')


# import time
# import shutil
# import pathlib
# import itertools

from torchvision.datasets import ImageFolder
from torch.utils.data import DataLoader, random_split, TensorDataset, Dataset
# import segmentation_models_pytorch as smp

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Mounted at /content/drive


## Prepare Load


In [ ]:
# def full_df(df_path):
#     classes = []
#     class_paths = []
#     files = os.listdir(df_path)
#     for file in files:
#         label_dir = os.path.join(df_path, file)
#         label = os.listdir(label_dir)
#         for image in label:
#             image_path = os.path.join(label_dir, image)
#             class_paths.append(image_path)
#             classes.append(file)
#     image_classes = pd.Series(classes, name='Class')
#     image_paths = pd.Series(class_paths, name='Class Path')
#     df = pd.concat([image_paths, image_classes], axis=1)
#     return df

# classes = []
# class_paths = []
# folders = os.listdir(df_path)
# for folder in folders:
#     folder_path = os.path.join(df_path, folder)
#     for image in os.listdir(folder_path):
#         image_path = os.path.join(folder_path, image)
#         class_paths.append(image_path)
#         classes.append(folder)
# image_classes = pd.Series(classes, name='Class')
# image_paths = pd.Series(class_paths, name='Class Path')
# df = pd.concat([image_paths, image_classes], axis=1)
# df

# df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/test'
# images = os.listdir(df_path)
# n = len(images)
# classes = ['']*n
# class_paths = ['']*n
# for i in range(n):
#     image_path = os.path.join(df_path, images[i])
#     class_paths[i] = image_path
#     classes[i] = (images[i][:images[i].find('-')])
# image_classes = pd.Series(classes, name='Class')
# image_paths = pd.Series(class_paths, name='Class Path')
# df = pd.concat([image_paths, image_classes], axis=1)
# df


# df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/test'
# classes = []
# class_paths = []
# for image in os.listdir(df_path):
#     image_path = os.path.join(df_path, image)
#     class_paths.append(image_path)
#     classes.append(image[:image.find('-')])
# image_classes = pd.Series(classes, name='Class')
# image_paths = pd.Series(class_paths, name='Class Path')
# df = pd.concat([image_paths, image_classes], axis=1)
# df

# ts_df = full_df('C:/Users/User/Downloads/archive/test')
# vld_df = full_df('C:/Users/User/Downloads/archive/training/val')
# tr_df = part_df('C:/Users/User/Downloads/archive/training/train')

In [ ]:
# import os
# import shutil
# import numpy as np

# # path0 = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset"
# # for folder in ['COVID', 'Lung_Opacity', 'Normal', 'Viral Pneumonia']:
# #     path = path0 + '/' + folder
# #     n = len(os.listdir(path + '/images'))
# #     d1, d2 = int(n * 0.7), int(n * 0.85)
# #     ar = np.arange(1, n + 1)
# #     np.random.shuffle(ar)
# #     os.mkdir(path + '/train')
# #     os.mkdir(path + '/val')
# #     os.mkdir(path + '/test')
# #     for i in ar[:d1]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path + '/train')
# #     print(folder, 'train')
# #     for i in ar[d1:d2]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path + '/val')
# #     print(folder, 'val')
# #     for i in ar[d2:]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path + '/test')
# #     print(folder, 'test')
# # path0 = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset"
# # os.mkdir(path0 + '/train')
# # os.mkdir(path0 + '/val')
# # os.mkdir(path0 + '/test')
# # for folder in ['COVID', 'Lung_Opacity', 'Normal', 'Viral Pneumonia']:
# #     path = path0 + '/' + folder
# #     n = len(os.listdir(path + '/images'))
# #     d1, d2 = int(n * 0.7), int(n * 0.85)
# #     ar = np.arange(1, n + 1)
# #     np.random.shuffle(ar)
# #     for i in ar[:d1]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path0 + '/train')
# #     print(folder, 'train')
# #     for i in ar[d1:d2]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path0 + '/val')
# #     print(folder, 'val')
# #     for i in ar[d2:]:
# #         filepath = path + f'/images/{folder}-{i}.png'
# #         shutil.copy(filepath, path0 + '/test')
# #     print(folder, 'test')

# # path0 = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset/df"
# # os.mkdir(path0)
# # for folder in ['train', 'val', 'test']:
# #     path = path0 + '/' + folder
# #     os.mkdir(path)
# #     for folder2 in ['COVID', 'Lung_Opacity', 'Normal', 'Viral Pneumonia']:
# #         path2 = path + '/' + folder2
# #         os.mkdir(path2)

# path0 = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset"
# for folder in ['train', 'val', 'test']:
#     path = path0 + '/' + folder
#     for im in os.listdir(path):
#         src = path + '/' + im
#         dist = path0 + '/df/' + folder + '/' + im[:im.find('-')] + '/' + im
#         shutil.copy(src, dist)
#     print(folder)


In [ ]:
# path_df = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset/df"
# path_masks = "C:/Users/User/Downloads/COVID-19_Radiography_Dataset"
# suf = '_masks'
# folders = ['train', 'val', 'test']
# subfolders = ['COVID', 'Lung_Opacity', 'Normal', 'Viral Pneumonia']
# for folder in folders:
#     print(folder)
#     path = path_df + '/' + folder
#     for subfolder in subfolders:
#         print(subfolder)
#         path_in = path_masks + '/' + subfolder + "/masks"
#         path_ex = path + '/' + subfolder
#         path_out = path + suf + '/' + subfolder
#         for im in os.listdir(path_ex):
#             src = path_in + '/' + im
#             dist = path_out + '/' + im
#             shutil.copy(src, dist)

In [ ]:
df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/val'
x_val = torch.zeros(3175, 1, 299, 299, dtype=torch.float16)
y_val = torch.zeros(3175, dtype=torch.int64)
tr = v2.ToTensor()
classes = {'COVID':0, 'Lung_Opacity':1,'Normal':2,'Viral Pneumonia':3}
i = -1
for folder in tqdm(os.listdir(df_path)):
    y = classes[folder]
    folder = f'{df_path}/{folder}'
    for file in tqdm(os.listdir(folder)):
        i += 1
        x_val[i] = tr(cv2.imread(f'{folder}/{file}'))[[0]]
        y_val[i] = y
torch.save(x_val, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_val.pt")
torch.save(y_val, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_val.pt")

/usr/local/lib/python3.11/dist-packages/torchvision/transforms/v2/_deprecated.py:42: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.Output is equivalent up to float precision.
  warnings.warn(


  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/1529 [00:00<?, ?it/s]

  0%|          | 0/902 [00:00<?, ?it/s]

  0%|          | 0/542 [00:00<?, ?it/s]

  0%|          | 0/202 [00:00<?, ?it/s]

In [ ]:
# df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/val'
# masks_path = df_path + '_masks'
# n = 0
# for folder in os.listdir(df_path):
#     n += len(os.listdir(f'{df_path}/{folder}'))

# x_val = torch.zeros(n, 1, 256, 256, dtype=torch.float16)
# masks_val = torch.zeros(n, 1, 256, 256, dtype=torch.bool)
# y_val = torch.zeros(n, dtype=torch.int64)
# image_size = (256, 256)
# tr_im = v2.Compose([
#     v2.ToTensor(),
#     v2.Resize(image_size)
# ])
# tr_mask = v2.ToTensor()
# classes = {'COVID':0, 'Lung_Opacity':1,'Normal':2,'Viral Pneumonia':3}
# i = -1
# for folder in os.listdir(df_path):
#     y = classes[folder]
#     folder_ims = f'{df_path}/{folder}'
#     folder_masks = f'{masks_path}/{folder}'
#     for file in tqdm(os.listdir(folder_ims), position=0, leave=True):
#         i += 1
#         x_val[i] = tr_im(cv2.imread(f'{folder_ims}/{file}'))[[0]]
#         masks_val[i] = tr_mask(cv2.imread(f'{folder_masks}/{file}'))[[0]]
#         y_val[i] = y
# collect()
# torch.save(x_val, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_val.pt")
# torch.save(masks_val, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/masks_val.pt")
# torch.save(y_val, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_val.pt")
# print(x_val.shape, masks_val.shape, y_val.shape)

In [ ]:
df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/train'
x_train = torch.zeros(14814, 1, 299, 299, dtype=torch.float16)
y_train = torch.zeros(14814, dtype=torch.int64)
tr = v2.ToTensor()
classes = {'COVID':0, 'Lung_Opacity':1,'Normal':2,'Viral Pneumonia':3}
i = -1
for folder in tqdm(os.listdir(df_path)):
    y = classes[folder]
    folder = f'{df_path}/{folder}'
    for file in tqdm(os.listdir(folder)):
        i += 1
        x_train[i] = tr(cv2.imread(f'{folder}/{file}'))[[0]]
        y_train[i] = y
    collect()
indices = torch.randperm(14814)
torch.save(x_train[indices], "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_train.pt")
torch.save(y_train[indices], "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_train.pt")

/usr/local/lib/python3.11/dist-packages/torchvision/transforms/v2/_deprecated.py:42: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.Output is equivalent up to float precision.
  warnings.warn(


  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/2531 [00:00<?, ?it/s]

  0%|          | 0/7135 [00:00<?, ?it/s]

  0%|          | 0/4208 [00:00<?, ?it/s]

  0%|          | 0/941 [00:00<?, ?it/s]

In [ ]:
df_path = '/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/test'
x_test = torch.zeros(3176, 1, 299, 299, dtype=torch.float16)
y_test = torch.zeros(3176, dtype=torch.int64)
tr = v2.ToTensor()
classes = {'COVID':0, 'Lung_Opacity':1,'Normal':2,'Viral Pneumonia':3}
i = -1
for folder in tqdm(os.listdir(df_path)):
    y = classes[folder]
    folder = f'{df_path}/{folder}'
    for file in tqdm(os.listdir(folder)):
        i += 1
        x_test[i] = tr(cv2.imread(f'{folder}/{file}'))[[0]]
        y_test[i] = y
torch.save(x_test, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_test.pt")
torch.save(y_test, "/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_test.pt")

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/543 [00:00<?, ?it/s]

  0%|          | 0/902 [00:00<?, ?it/s]

  0%|          | 0/1529 [00:00<?, ?it/s]

  0%|          | 0/202 [00:00<?, ?it/s]

In [ ]:
collect()

153

## Load

In [ ]:
class MyDataset(Dataset):
    def __init__(self, data, target, transform=None, target_transform=None):
        self.data = data
        self.target = target
        self.transform = transform
        self.target_transform = target_transform

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        x = self.data[index]
        if self.transform:
            x = self.transform(x)

        y = self.target[index]
        if self.target_transform:
            y = self.target_transform(y)

        return x, y

In [ ]:
x_train = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_train.pt")
y_train = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_train.pt")
x_val = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_val.pt")
y_val = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_val.pt")
x_test = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_test.pt")
y_test = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_test.pt")

df_train = MyDataset(x_train, y_train.long())
df_val = MyDataset(x_val, y_val.long())
df_test = MyDataset(x_test, y_test.long())

In [ ]:
# image_size = (299, 299)

train_transforms = v2.Compose([
    # v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    # v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms
df_test.transform = val_transforms

In [ ]:
batch_size = 16

train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(df_test, batch_size=batch_size, shuffle=False)

print("Train set size:", len(df_train))
print("Val set size:", len(df_val))

Train set size: 14815
Val set size: 3175


In [ ]:
def train_val(model, optimizer, criterion, scheduler, epochs, train_loader, val_loader, train_size, val_size):
    pbar = trange(epochs, desc="Epoch:")
    for epoch in pbar:
        train_correct = 0
        val_correct = 0

        model.train()
        for inputs, targets in tqdm(train_loader):
            optimizer.zero_grad()
            with torch.autocast(device_type="cuda", dtype=torch.float16):
                if inputs.shape[1] == 1:
                    outputs = model(inputs.to(device).expand(-1,3,-1,-1))
                else:
                    outputs = model(inputs.to(device))

            targets = targets.to(device) ##.squeeze().long()

            loss = criterion(outputs, targets)
            loss.backward()
            optimizer.step()
            preds = torch.argmax(outputs, 1)
            train_correct +=  torch.sum(preds == targets).item()
        train_acc = train_correct / train_size
        if scheduler:
            scheduler.step()

        model.eval()
        with torch.no_grad():
            for inputs, targets in val_loader:
                with torch.autocast(device_type="cuda", dtype=torch.float16):
                    if inputs.shape[1] == 1:
                        outputs = model(inputs.to(device).expand(-1,3,-1,-1))
                    else:
                        outputs = model(inputs.to(device))

                targets = targets.to(device) ##.squeeze().long()
                preds = torch.argmax(outputs, 1)
                val_correct +=  torch.sum(preds == targets).item()
        val_acc = val_correct / val_size
        print(f'Epoch {epoch + 1}) train acc: {round(100 * train_acc, 2)}, val acc: {round(100 * val_acc, 2)}')

def test(model, criterion, test_loader, test_size):
    model.eval()
    test_correct = 0
    with torch.no_grad():
        for inputs, targets in test_loader:
            with torch.autocast(device_type="cuda", dtype=torch.float16):
                if inputs.shape[1] == 1:
                    outputs = model(inputs.to(device).expand(-1,3,-1,-1))
                else:
                    outputs = model(inputs.to(device))

            targets = targets.squeeze().long().to(device)
            preds = torch.argmax(outputs, 1)
            test_correct +=  torch.sum(preds == targets).item()
    test_acc = test_correct / test_size
    print(f'Test acc: {round(100 * test_acc, 2)}')

In [ ]:
# test_path = 'C:/Users/User/Downloads/COVID-19_Radiography_Dataset/df/test'
# df_test = ImageFolder(test_path)
# df_test.transform = val_transforms
# test_loader = DataLoader(df_test, batch_size=batch_size, shuffle=False)
# print("Test set size:", len(df_test))
# test(model=model, criterion=criterion, test_loader=test_loader, test_size=len(df_test))

## Choose Classification Model

### vgg19_bn 26m 90.05

In [ ]:
model = models.vgg19_bn(weights='IMAGENET1K_V1')
model.classifier =  nn.Sequential(
          nn.Linear(in_features=25088, out_features=256, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=256, out_features=4, bias=True),
        )
model.to(device)
sum(p.numel() for p in model.parameters())

26459204

In [ ]:
criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 77.68, val acc: 84.09


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 87.09, val acc: 81.35


...

Epoch 3) train acc: 90.39, val acc: 90.05


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 91.25, val acc: 86.3


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 92.08, val acc: 86.2


### resnet50 24m 90.46

In [ ]:
model = models.resnet50(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=2048, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 23639428


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 83.9, val acc: 90.24


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 91.68, val acc: 84.72


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 92.8, val acc: 86.52


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.78, val acc: 89.26


### inception_v3 25m 92.57

In [ ]:
def train_val_inception(model, optimizer, criterion, scheduler, epochs, train_loader, val_loader, train_size, val_size):
    pbar = trange(epochs, desc="Epoch:")
    for epoch in pbar:
        train_correct = 0
        val_correct = 0

        model.train()
        for inputs, targets in tqdm(train_loader):
            optimizer.zero_grad()
            with torch.autocast(device_type="cuda", dtype=torch.float16):
                outputs, _ = model(inputs.to(device).expand(-1,3,-1,-1))

            targets = targets.to(device) ##.squeeze().long()

            loss = criterion(outputs, targets)
            loss.backward()
            optimizer.step()
            preds = torch.argmax(outputs, 1)
            train_correct +=  torch.sum(preds == targets).item()
        train_acc = train_correct / train_size
        if scheduler:
            scheduler.step()

        model.eval()
        with torch.no_grad():
            for inputs, targets in val_loader:
                with torch.autocast(device_type="cuda", dtype=torch.float16):
                    outputs = model(inputs.to(device).expand(-1,3,-1,-1))

                targets = targets.to(device) ##.squeeze().long()
                preds = torch.argmax(outputs, 1)
                val_correct +=  torch.sum(preds == targets).item()
        val_acc = val_correct / val_size
        print(f'Epoch {epoch + 1}) train acc: {round(100 * train_acc, 2)}, val acc: {round(100 * val_acc, 2)}')

In [ ]:
model = models.inception_v3(weights='IMAGENET1K_V1')
model.dropout = nn.Identity()
model.fc =  nn.Sequential(
          nn.Linear(in_features=2048, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val_inception(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 25243660


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 84.55, val acc: 89.23


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 92.17, val acc: 92.57


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 93.1, val acc: 92.35


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.49, val acc: 91.37


### wide_resnet50_2 67m 90.43


In [ ]:
model = models.wide_resnet50_2(weights='IMAGENET1K_V2')

Downloading: "https://download.pytorch.org/models/wide_resnet50_2-9ba9bcbe.pth" to /root/.cache/torch/hub/checkpoints/wide_resnet50_2-9ba9bcbe.pth
100%|██████████| 263M/263M [00:01<00:00, 164MB/s]


In [ ]:
model = models.wide_resnet50_2(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=2048, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 66965636


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 84.52, val acc: 84.47


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 91.3, val acc: 88.66


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 93.14, val acc: 84.66


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.44, val acc: 90.43


### resnext50_32x4d 23m 92.35

In [ ]:
model = models.resnext50_32x4d(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=2048, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 23111300


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.98, val acc: 92.35


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.42, val acc: 90.05


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.36, val acc: 89.42


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.19, val acc: 89.61


### densenet201 18m 92.31+

In [ ]:
model = models.densenet201(weights='IMAGENET1K_V1')
model.classifier =  nn.Sequential(
          nn.Linear(in_features=1920, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18216132


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 81.69, val acc: 82.55


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 90.75, val acc: 91.31


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 92.23, val acc: 92.06


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.03, val acc: 92.31


### mobilenet_v3_large 3m 93.61

In [ ]:
model = models.mobilenet_v3_large(weights='IMAGENET1K_V2')
model.classifier =  nn.Sequential(
          nn.Linear(in_features=960, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
sum(p.numel() for p in model.parameters())

3033716

In [ ]:
model = models.mobilenet_v3_large(weights='IMAGENET1K_V2')
model.classifier =  nn.Sequential(
          nn.Linear(in_features=960, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))
criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 3033716


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 89.36, val acc: 92.66


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 95.15, val acc: 90.49


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.61, val acc: 93.61


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 96.46, val acc: 84.79


### regnet_y_1_6gf 10m 91.87

In [ ]:
model = models.regnet_y_1_6gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=888, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 10370586


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.19, val acc: 90.05


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.43, val acc: 88.94


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.88, val acc: 91.87


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.19, val acc: 90.3


### regnet_y_3_2gf 18m 94.36/93.895

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.72, val acc: 91.53


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 94.03, val acc: 93.01


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.94, val acc: 92.79


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.54, val acc: 94.36


### regnet_y_8gf 37m 91.84

In [ ]:
model = models.regnet_y_8gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=2016, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 37493820


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.66, val acc: 89.42


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.23, val acc: 87.31


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.13, val acc: 89.42


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.94, val acc: 91.37


### efficientnet_v2_s 20m  93.95

In [ ]:
model = models.efficientnet_v2_s(weights='IMAGENET1K_V1')
model.classifier =  nn.Sequential(
          nn.Linear(in_features=1280, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))
criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 20259732


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.43, val acc: 89.92


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 92.49, val acc: 92.98


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 93.72, val acc: 84.88


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.69, val acc: 87.69


### swin_v2_t 28m 93.32

In [ ]:
model = models.swin_v2_t(weights='IMAGENET1K_V1')
model.head =  nn.Sequential(
          nn.Linear(in_features=768, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 27632046


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.47, val acc: 86.99


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.93, val acc: 88.16


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.95, val acc: 90.52


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.48, val acc: 88.91


### convnext_tiny 28m 93.20


In [ ]:
model = models.convnext_tiny(weights='IMAGENET1K_V1')
model.classifier[2] = nn.Sequential(
          nn.Linear(in_features=768, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 27823204


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 83.92, val acc: 89.35


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 91.36, val acc: 92.0


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 92.41, val acc: 92.09


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.05, val acc: 93.2


### maxvit_t 30m 88.19

In [ ]:
image_size = (224, 224)

train_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16

train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

print("Train set size:", len(df_train))
print("Val set size:", len(df_val))

Train set size: 14815
Val set size: 3175


In [ ]:
model = models.maxvit_t(weights='IMAGENET1K_V1')
model.classifier[3] =  nn.Linear(in_features=512, out_features=128, bias=True)
model.classifier[4] =  nn.ReLU()
model.classifier[5] =  nn.Linear(in_features=128, out_features=4, bias=True)
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 30211148


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 84.28, val acc: 88.19


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 91.11, val acc: 86.39


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 69.68, val acc: 17.07


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 17.08, val acc: 17.07


### TinyViT

https://github.com/wkcn/TinyViT

In [ ]:
# --------------------------------------------------------
# TinyViT Model Architecture
# Copyright (c) 2022 Microsoft
# Adapted from LeViT and Swin Transformer
#   LeViT: (https://github.com/facebookresearch/levit)
#   Swin: (https://github.com/microsoft/swin-transformer)
# Build the TinyViT Model
# --------------------------------------------------------

import itertools
from typing import Tuple
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.checkpoint as checkpoint
import timm
from timm.models.layers import DropPath as TimmDropPath,\
    to_2tuple, trunc_normal_
from timm.models.registry import register_model
try:
    # timm.__version__ >= "0.6"
    from timm.models._builder import build_model_with_cfg
except (ImportError, ModuleNotFoundError):
    # timm.__version__ < "0.6"
    from timm.models.helpers import build_model_with_cfg


class Conv2d_BN(torch.nn.Sequential):
    def __init__(self, a, b, ks=1, stride=1, pad=0, dilation=1,
                 groups=1, bn_weight_init=1):
        super().__init__()
        self.add_module('c', torch.nn.Conv2d(
            a, b, ks, stride, pad, dilation, groups, bias=False))
        bn = torch.nn.BatchNorm2d(b)
        torch.nn.init.constant_(bn.weight, bn_weight_init)
        torch.nn.init.constant_(bn.bias, 0)
        self.add_module('bn', bn)

    @torch.no_grad()
    def fuse(self):
        c, bn = self._modules.values()
        w = bn.weight / (bn.running_var + bn.eps)**0.5
        w = c.weight * w[:, None, None, None]
        b = bn.bias - bn.running_mean * bn.weight / \
            (bn.running_var + bn.eps)**0.5
        m = torch.nn.Conv2d(w.size(1) * self.c.groups, w.size(
            0), w.shape[2:], stride=self.c.stride, padding=self.c.padding, dilation=self.c.dilation, groups=self.c.groups)
        m.weight.data.copy_(w)
        m.bias.data.copy_(b)
        return m


class DropPath(TimmDropPath):
    def __init__(self, drop_prob=None):
        super().__init__(drop_prob=drop_prob)
        self.drop_prob = drop_prob

    def __repr__(self):
        msg = super().__repr__()
        msg += f'(drop_prob={self.drop_prob})'
        return msg


class PatchEmbed(nn.Module):
    def __init__(self, in_chans, embed_dim, resolution, activation):
        super().__init__()
        img_size: Tuple[int, int] = to_2tuple(resolution)
        self.patches_resolution = (img_size[0] // 4, img_size[1] // 4)
        self.num_patches = self.patches_resolution[0] * \
            self.patches_resolution[1]
        self.in_chans = in_chans
        self.embed_dim = embed_dim
        n = embed_dim
        self.seq = nn.Sequential(
            Conv2d_BN(in_chans, n // 2, 3, 2, 1),
            activation(),
            Conv2d_BN(n // 2, n, 3, 2, 1),
        )

    def forward(self, x):
        return self.seq(x)


class MBConv(nn.Module):
    def __init__(self, in_chans, out_chans, expand_ratio,
                 activation, drop_path):
        super().__init__()
        self.in_chans = in_chans
        self.hidden_chans = int(in_chans * expand_ratio)
        self.out_chans = out_chans

        self.conv1 = Conv2d_BN(in_chans, self.hidden_chans, ks=1)
        self.act1 = activation()

        self.conv2 = Conv2d_BN(self.hidden_chans, self.hidden_chans,
                               ks=3, stride=1, pad=1, groups=self.hidden_chans)
        self.act2 = activation()

        self.conv3 = Conv2d_BN(
            self.hidden_chans, out_chans, ks=1, bn_weight_init=0.0)
        self.act3 = activation()

        self.drop_path = DropPath(
            drop_path) if drop_path > 0. else nn.Identity()

    def forward(self, x):
        shortcut = x

        x = self.conv1(x)
        x = self.act1(x)

        x = self.conv2(x)
        x = self.act2(x)

        x = self.conv3(x)

        x = self.drop_path(x)

        x += shortcut
        x = self.act3(x)

        return x


class PatchMerging(nn.Module):
    def __init__(self, input_resolution, dim, out_dim, activation):
        super().__init__()

        self.input_resolution = input_resolution
        self.dim = dim
        self.out_dim = out_dim
        self.act = activation()
        self.conv1 = Conv2d_BN(dim, out_dim, 1, 1, 0)
        self.conv2 = Conv2d_BN(out_dim, out_dim, 3, 2, 1, groups=out_dim)
        self.conv3 = Conv2d_BN(out_dim, out_dim, 1, 1, 0)

    def forward(self, x):
        if x.ndim == 3:
            H, W = self.input_resolution
            B = len(x)
            # (B, C, H, W)
            x = x.view(B, H, W, -1).permute(0, 3, 1, 2)

        x = self.conv1(x)
        x = self.act(x)
        x = self.conv2(x)
        x = self.act(x)
        x = self.conv3(x)

        x = x.flatten(2).transpose(1, 2)
        return x


class ConvLayer(nn.Module):
    def __init__(self, dim, input_resolution, depth,
                 activation,
                 drop_path=0., downsample=None, use_checkpoint=False,
                 out_dim=None,
                 conv_expand_ratio=4.,
                 ):

        super().__init__()
        self.dim = dim
        self.input_resolution = input_resolution
        self.depth = depth
        self.use_checkpoint = use_checkpoint

        # build blocks
        self.blocks = nn.ModuleList([
            MBConv(dim, dim, conv_expand_ratio, activation,
                   drop_path[i] if isinstance(drop_path, list) else drop_path,
                   )
            for i in range(depth)])

        # patch merging layer
        if downsample is not None:
            self.downsample = downsample(
                input_resolution, dim=dim, out_dim=out_dim, activation=activation)
        else:
            self.downsample = None

    def forward(self, x):
        for blk in self.blocks:
            if self.use_checkpoint:
                x = checkpoint.checkpoint(blk, x)
            else:
                x = blk(x)
        if self.downsample is not None:
            x = self.downsample(x)
        return x


class Mlp(nn.Module):
    def __init__(self, in_features, hidden_features=None,
                 out_features=None, act_layer=nn.GELU, drop=0.):
        super().__init__()
        out_features = out_features or in_features
        hidden_features = hidden_features or in_features
        self.norm = nn.LayerNorm(in_features)
        self.fc1 = nn.Linear(in_features, hidden_features)
        self.fc2 = nn.Linear(hidden_features, out_features)
        self.act = act_layer()
        self.drop = nn.Dropout(drop)

    def forward(self, x):
        x = self.norm(x)

        x = self.fc1(x)
        x = self.act(x)
        x = self.drop(x)
        x = self.fc2(x)
        x = self.drop(x)
        return x


class Attention(torch.nn.Module):
    def __init__(self, dim, key_dim, num_heads=8,
                 attn_ratio=4,
                 resolution=(14, 14),
                 ):
        super().__init__()
        # (h, w)
        assert isinstance(resolution, tuple) and len(resolution) == 2
        self.num_heads = num_heads
        self.scale = key_dim ** -0.5
        self.key_dim = key_dim
        self.nh_kd = nh_kd = key_dim * num_heads
        self.d = int(attn_ratio * key_dim)
        self.dh = int(attn_ratio * key_dim) * num_heads
        self.attn_ratio = attn_ratio
        h = self.dh + nh_kd * 2

        self.norm = nn.LayerNorm(dim)
        self.qkv = nn.Linear(dim, h)
        self.proj = nn.Linear(self.dh, dim)

        points = list(itertools.product(
            range(resolution[0]), range(resolution[1])))
        N = len(points)
        attention_offsets = {}
        idxs = []
        for p1 in points:
            for p2 in points:
                offset = (abs(p1[0] - p2[0]), abs(p1[1] - p2[1]))
                if offset not in attention_offsets:
                    attention_offsets[offset] = len(attention_offsets)
                idxs.append(attention_offsets[offset])
        self.attention_biases = torch.nn.Parameter(
            torch.zeros(num_heads, len(attention_offsets)))
        self.register_buffer('attention_bias_idxs',
                             torch.LongTensor(idxs).view(N, N),
                             persistent=False)

    @torch.no_grad()
    def train(self, mode=True):
        super().train(mode)
        if mode and hasattr(self, 'ab'):
            del self.ab
        else:
            self.ab = self.attention_biases[:, self.attention_bias_idxs]

    def forward(self, x):  # x (B,N,C)
        B, N, _ = x.shape

        # Normalization
        x = self.norm(x)

        qkv = self.qkv(x)
        # (B, N, num_heads, d)
        q, k, v = qkv.view(B, N, self.num_heads, -
                           1).split([self.key_dim, self.key_dim, self.d], dim=3)
        # (B, num_heads, N, d)
        q = q.permute(0, 2, 1, 3)
        k = k.permute(0, 2, 1, 3)
        v = v.permute(0, 2, 1, 3)

        attn = (
            (q @ k.transpose(-2, -1)) * self.scale
            +
            (self.attention_biases[:, self.attention_bias_idxs]
             if self.training else self.ab)
        )
        attn = attn.softmax(dim=-1)
        x = (attn @ v).transpose(1, 2).reshape(B, N, self.dh)
        x = self.proj(x)
        return x


class TinyViTBlock(nn.Module):
    r""" TinyViT Block.

    Args:
        dim (int): Number of input channels.
        input_resolution (tuple[int, int]): Input resulotion.
        num_heads (int): Number of attention heads.
        window_size (int): Window size.
        mlp_ratio (float): Ratio of mlp hidden dim to embedding dim.
        drop (float, optional): Dropout rate. Default: 0.0
        drop_path (float, optional): Stochastic depth rate. Default: 0.0
        local_conv_size (int): the kernel size of the convolution between
                               Attention and MLP. Default: 3
        activation: the activation function. Default: nn.GELU
    """

    def __init__(self, dim, input_resolution, num_heads, window_size=7,
                 mlp_ratio=4., drop=0., drop_path=0.,
                 local_conv_size=3,
                 activation=nn.GELU,
                 ):
        super().__init__()
        self.dim = dim
        self.input_resolution = input_resolution
        self.num_heads = num_heads
        assert window_size > 0, 'window_size must be greater than 0'
        self.window_size = window_size
        self.mlp_ratio = mlp_ratio

        self.drop_path = DropPath(
            drop_path) if drop_path > 0. else nn.Identity()

        assert dim % num_heads == 0, 'dim must be divisible by num_heads'
        head_dim = dim // num_heads

        window_resolution = (window_size, window_size)
        self.attn = Attention(dim, head_dim, num_heads,
                              attn_ratio=1, resolution=window_resolution)

        mlp_hidden_dim = int(dim * mlp_ratio)
        mlp_activation = activation
        self.mlp = Mlp(in_features=dim, hidden_features=mlp_hidden_dim,
                       act_layer=mlp_activation, drop=drop)

        pad = local_conv_size // 2
        self.local_conv = Conv2d_BN(
            dim, dim, ks=local_conv_size, stride=1, pad=pad, groups=dim)

    def forward(self, x):
        H, W = self.input_resolution
        B, L, C = x.shape
        assert L == H * W, "input feature has wrong size"
        res_x = x
        if H == self.window_size and W == self.window_size:
            x = self.attn(x)
        else:
            x = x.view(B, H, W, C)
            pad_b = (self.window_size - H %
                     self.window_size) % self.window_size
            pad_r = (self.window_size - W %
                     self.window_size) % self.window_size
            padding = pad_b > 0 or pad_r > 0

            if padding:
                x = F.pad(x, (0, 0, 0, pad_r, 0, pad_b))

            pH, pW = H + pad_b, W + pad_r
            nH = pH // self.window_size
            nW = pW // self.window_size
            # window partition
            x = x.view(B, nH, self.window_size, nW, self.window_size, C).transpose(2, 3).reshape(
                B * nH * nW, self.window_size * self.window_size, C
            )
            x = self.attn(x)
            # window reverse
            x = x.view(B, nH, nW, self.window_size, self.window_size,
                       C).transpose(2, 3).reshape(B, pH, pW, C)

            if padding:
                x = x[:, :H, :W].contiguous()

            x = x.view(B, L, C)

        x = res_x + self.drop_path(x)

        x = x.transpose(1, 2).reshape(B, C, H, W)
        x = self.local_conv(x)
        x = x.view(B, C, L).transpose(1, 2)

        x = x + self.drop_path(self.mlp(x))
        return x

    def extra_repr(self) -> str:
        return f"dim={self.dim}, input_resolution={self.input_resolution}, num_heads={self.num_heads}, " \
               f"window_size={self.window_size}, mlp_ratio={self.mlp_ratio}"


class BasicLayer(nn.Module):
    """ A basic TinyViT layer for one stage.

    Args:
        dim (int): Number of input channels.
        input_resolution (tuple[int]): Input resolution.
        depth (int): Number of blocks.
        num_heads (int): Number of attention heads.
        window_size (int): Local window size.
        mlp_ratio (float): Ratio of mlp hidden dim to embedding dim.
        drop (float, optional): Dropout rate. Default: 0.0
        drop_path (float | tuple[float], optional): Stochastic depth rate. Default: 0.0
        downsample (nn.Module | None, optional): Downsample layer at the end of the layer. Default: None
        use_checkpoint (bool): Whether to use checkpointing to save memory. Default: False.
        local_conv_size: the kernel size of the depthwise convolution between attention and MLP. Default: 3
        activation: the activation function. Default: nn.GELU
        out_dim: the output dimension of the layer. Default: dim
    """

    def __init__(self, dim, input_resolution, depth, num_heads, window_size,
                 mlp_ratio=4., drop=0.,
                 drop_path=0., downsample=None, use_checkpoint=False,
                 local_conv_size=3,
                 activation=nn.GELU,
                 out_dim=None,
                 ):

        super().__init__()
        self.dim = dim
        self.input_resolution = input_resolution
        self.depth = depth
        self.use_checkpoint = use_checkpoint

        # build blocks
        self.blocks = nn.ModuleList([
            TinyViTBlock(dim=dim, input_resolution=input_resolution,
                         num_heads=num_heads, window_size=window_size,
                         mlp_ratio=mlp_ratio,
                         drop=drop,
                         drop_path=drop_path[i] if isinstance(
                             drop_path, list) else drop_path,
                         local_conv_size=local_conv_size,
                         activation=activation,
                         )
            for i in range(depth)])

        # patch merging layer
        if downsample is not None:
            self.downsample = downsample(
                input_resolution, dim=dim, out_dim=out_dim, activation=activation)
        else:
            self.downsample = None

    def forward(self, x):
        for blk in self.blocks:
            if self.use_checkpoint:
                x = checkpoint.checkpoint(blk, x)
            else:
                x = blk(x)
        if self.downsample is not None:
            x = self.downsample(x)
        return x

    def extra_repr(self) -> str:
        return f"dim={self.dim}, input_resolution={self.input_resolution}, depth={self.depth}"


class TinyViT(nn.Module):
    def __init__(self, img_size=224, in_chans=3, num_classes=1000,
                 embed_dims=[96, 192, 384, 768], depths=[2, 2, 6, 2],
                 num_heads=[3, 6, 12, 24],
                 window_sizes=[7, 7, 14, 7],
                 mlp_ratio=4.,
                 drop_rate=0.,
                 drop_path_rate=0.1,
                 use_checkpoint=False,
                 mbconv_expand_ratio=4.0,
                 local_conv_size=3,
                 layer_lr_decay=1.0,
                 ):
        super().__init__()

        self.num_classes = num_classes
        self.depths = depths
        self.num_layers = len(depths)
        self.mlp_ratio = mlp_ratio

        activation = nn.GELU

        self.patch_embed = PatchEmbed(in_chans=in_chans,
                                      embed_dim=embed_dims[0],
                                      resolution=img_size,
                                      activation=activation)

        patches_resolution = self.patch_embed.patches_resolution
        self.patches_resolution = patches_resolution

        # stochastic depth
        dpr = [x.item() for x in torch.linspace(0, drop_path_rate,
                                                sum(depths))]  # stochastic depth decay rule

        # build layers
        self.layers = nn.ModuleList()
        for i_layer in range(self.num_layers):
            kwargs = dict(dim=embed_dims[i_layer],
                          input_resolution=(patches_resolution[0] // (2 ** i_layer),
                                            patches_resolution[1] // (2 ** i_layer)),
                          depth=depths[i_layer],
                          drop_path=dpr[sum(depths[:i_layer]):sum(depths[:i_layer + 1])],
                          downsample=PatchMerging if (
                              i_layer < self.num_layers - 1) else None,
                          use_checkpoint=use_checkpoint,
                          out_dim=embed_dims[min(
                              i_layer + 1, len(embed_dims) - 1)],
                          activation=activation,
                          )
            if i_layer == 0:
                layer = ConvLayer(
                    conv_expand_ratio=mbconv_expand_ratio,
                    **kwargs,
                )
            else:
                layer = BasicLayer(
                    num_heads=num_heads[i_layer],
                    window_size=window_sizes[i_layer],
                    mlp_ratio=self.mlp_ratio,
                    drop=drop_rate,
                    local_conv_size=local_conv_size,
                    **kwargs)
            self.layers.append(layer)

        # Classifier head
        self.norm_head = nn.LayerNorm(embed_dims[-1])
        self.head = nn.Linear(
            embed_dims[-1], num_classes) if num_classes > 0 else torch.nn.Identity()

        # init weights
        self.apply(self._init_weights)
        self.set_layer_lr_decay(layer_lr_decay)

    def set_layer_lr_decay(self, layer_lr_decay):
        decay_rate = layer_lr_decay

        # layers -> blocks (depth)
        depth = sum(self.depths)
        lr_scales = [decay_rate ** (depth - i - 1) for i in range(depth)]

        def _set_lr_scale(m, scale):
            for p in m.parameters():
                p.lr_scale = scale

        self.patch_embed.apply(lambda x: _set_lr_scale(x, lr_scales[0]))
        i = 0
        for layer in self.layers:
            for block in layer.blocks:
                block.apply(lambda x: _set_lr_scale(x, lr_scales[i]))
                i += 1
            if layer.downsample is not None:
                layer.downsample.apply(
                    lambda x: _set_lr_scale(x, lr_scales[i - 1]))
        assert i == depth
        for m in [self.norm_head, self.head]:
            m.apply(lambda x: _set_lr_scale(x, lr_scales[-1]))

        for k, p in self.named_parameters():
            p.param_name = k

        def _check_lr_scale(m):
            for p in m.parameters():
                assert hasattr(p, 'lr_scale'), p.param_name

        self.apply(_check_lr_scale)

    def _init_weights(self, m):
        if isinstance(m, nn.Linear):
            trunc_normal_(m.weight, std=.02)
            if isinstance(m, nn.Linear) and m.bias is not None:
                nn.init.constant_(m.bias, 0)
        elif isinstance(m, nn.LayerNorm):
            nn.init.constant_(m.bias, 0)
            nn.init.constant_(m.weight, 1.0)

    @torch.jit.ignore
    def no_weight_decay_keywords(self):
        return {'attention_biases'}

    def forward_features(self, x):
        # x: (N, C, H, W)
        x = self.patch_embed(x)

        x = self.layers[0](x)
        start_i = 1

        for i in range(start_i, len(self.layers)):
            layer = self.layers[i]
            x = layer(x)

        x = x.mean(1)

        return x

    def forward(self, x):
        x = self.forward_features(x)
        x = self.norm_head(x)
        x = self.head(x)
        return x


_checkpoint_url_format = \
    'https://github.com/wkcn/TinyViT-model-zoo/releases/download/checkpoints/{}.pth'


def _create_tiny_vit(variant, pretrained=False, **kwargs):
    # pretrained_type: 22kto1k_distill, 1k, 22k_distill
    pretrained_type = kwargs.pop('pretrained_type', '22kto1k_distill')
    assert pretrained_type in ['22kto1k_distill', '1k', '22k_distill'], \
        'pretrained_type should be one of 22kto1k_distill, 1k, 22k_distill'

    img_size = kwargs.get('img_size', 224)
    if img_size != 224:
        pretrained_type = pretrained_type.replace('_', f'_{img_size}_')

    num_classes_pretrained = 21841 if \
        pretrained_type  == '22k_distill' else 1000

    variant_without_img_size = '_'.join(variant.split('_')[:-1])
    cfg = dict(
        url=_checkpoint_url_format.format(
            f'{variant_without_img_size}_{pretrained_type}'),
        num_classes=num_classes_pretrained,
        classifier='head',
    )

    def _pretrained_filter_fn(state_dict):
        state_dict = state_dict['model']
        # filter out attention_bias_idxs
        state_dict = {k: v for k, v in state_dict.items() if \
            not k.endswith('attention_bias_idxs')}
        return state_dict

    if timm.__version__ >= "0.6":
        return build_model_with_cfg(
            TinyViT, variant, pretrained,
            pretrained_cfg=cfg,
            pretrained_filter_fn=_pretrained_filter_fn,
            **kwargs)
    else:
        return build_model_with_cfg(
            TinyViT, variant, pretrained,
            default_cfg=cfg,
            pretrained_filter_fn=_pretrained_filter_fn,
            **kwargs)


@register_model
def tiny_vit_5m_224(pretrained=False, **kwargs):
    model_kwargs = dict(
        embed_dims=[64, 128, 160, 320],
        depths=[2, 2, 6, 2],
        num_heads=[2, 4, 5, 10],
        window_sizes=[7, 7, 14, 7],
        drop_path_rate=0.0,
    )
    model_kwargs.update(kwargs)
    return _create_tiny_vit('tiny_vit_5m_224', pretrained, **model_kwargs)


@register_model
def tiny_vit_11m_224(pretrained=False, **kwargs):
    model_kwargs = dict(
        embed_dims=[64, 128, 256, 448],
        depths=[2, 2, 6, 2],
        num_heads=[2, 4, 8, 14],
        window_sizes=[7, 7, 14, 7],
        drop_path_rate=0.1,
    )
    model_kwargs.update(kwargs)
    return _create_tiny_vit('tiny_vit_11m_224', pretrained, **model_kwargs)


@register_model
def tiny_vit_21m_224(pretrained=False, **kwargs):
    model_kwargs = dict(
        embed_dims=[96, 192, 384, 576],
        depths=[2, 2, 6, 2],
        num_heads=[3, 6, 12, 18],
        window_sizes=[7, 7, 14, 7],
        drop_path_rate=0.2,
    )
    model_kwargs.update(kwargs)
    return _create_tiny_vit('tiny_vit_21m_224', pretrained, **model_kwargs)


@register_model
def tiny_vit_21m_384(pretrained=False, **kwargs):
    model_kwargs = dict(
        img_size=384,
        embed_dims=[96, 192, 384, 576],
        depths=[2, 2, 6, 2],
        num_heads=[3, 6, 12, 18],
        window_sizes=[12, 12, 24, 12],
        drop_path_rate=0.1,
    )
    model_kwargs.update(kwargs)
    return _create_tiny_vit('tiny_vit_21m_384', pretrained, **model_kwargs)


@register_model
def tiny_vit_21m_512(pretrained=False, **kwargs):
    model_kwargs = dict(
        img_size=512,
        embed_dims=[96, 192, 384, 576],
        depths=[2, 2, 6, 2],
        num_heads=[3, 6, 12, 18],
        window_sizes=[16, 16, 32, 16],
        drop_path_rate=0.1,
    )
    model_kwargs.update(kwargs)
    return _create_tiny_vit('tiny_vit_21m_512', pretrained, **model_kwargs)

/usr/local/lib/python3.11/dist-packages/timm/models/layers/__init__.py:48: FutureWarning: Importing from timm.models.layers is deprecated, please import via timm.layers
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.layers", FutureWarning)
/usr/local/lib/python3.11/dist-packages/timm/models/registry.py:4: FutureWarning: Importing from timm.models.registry is deprecated, please import via timm.models
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.models", FutureWarning)
<ipython-input-16-0271c1f4dca4>:640: UserWarning: Overwriting tiny_vit_5m_224 in registry with __main__.tiny_vit_5m_224. This is because the name being registered conflicts with an existing name. Please check if this is not expected.
  @register_model
<ipython-input-16-0271c1f4dca4>:653: UserWarning: Overwriting tiny_vit_11m_224 in registry with __main__.tiny_vit_11m_224. This is because the name being registered conflicts with an existing name. Please

In [ ]:
image_size = (224, 224)

train_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16

train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

print("Train set size:", len(df_train))
print("Val set size:", len(df_val))

Train set size: 14815
Val set size: 3175


### tiny_vit_21m_224 21M 93.45

In [ ]:
model = tiny_vit_21m_224(pretrained=True)
model.head =  nn.Sequential(
          nn.Linear(in_features=576, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 20658756


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 83.16, val acc: 92.57


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 91.91, val acc: 92.6


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 93.25, val acc: 92.19


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.75, val acc: 93.2


### tiny_vit_11m_224 11M 93.95

In [ ]:
model = tiny_vit_11m_224(pretrained=True)
model.head =  nn.Sequential(
          nn.Linear(in_features=448, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 10576968


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 71.92, val acc: 84.38


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 88.48, val acc: 93.95


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 90.81, val acc: 93.07


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 90.75, val acc: 88.72


### tiny_vit_5m_224 5M 93.32+

In [ ]:
model = tiny_vit_5m_224(pretrained=True)
model.head =  nn.Sequential(
          nn.Linear(in_features=320, out_features=32, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=32, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 5082168


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 85.04, val acc: 91.5


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 92.6, val acc: 91.84


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 92.43, val acc: 92.38


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 93.83, val acc: 93.32


### tiny_vit_21m_384 21M 93.45

In [ ]:
image_size = (384, 384)

train_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16

train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

print("Train set size:", len(df_train))
print("Val set size:", len(df_val))

Train set size: 14815
Val set size: 3175


In [ ]:
model = tiny_vit_21m_384(pretrained=True)
model.head =  nn.Sequential(
          nn.Linear(in_features=576, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Downloading: "https://github.com/wkcn/TinyViT-model-zoo/releases/download/checkpoints/tiny_vit_21m_22kto1k_384_distill.pth" to /root/.cache/torch/hub/checkpoints/tiny_vit_21m_22kto1k_384_distill.pth


Number of parameters: 20690676


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 85.21, val acc: 92.5


...

Epoch 3) train acc: 91.98, val acc: 92.85


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 89.74, val acc: 78.9


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 89.2, val acc: 93.45


### mobilenetv4 pretrained model

https://blog.roboflow.com/how-to-use-mobilenetv4-for-classification/

https://github.com/jiaowoguanren0615/MobileNetV4

https://huggingface.co/collections/timm/mobilenetv4-pretrained-weights-6669c22cda4db4244def9637

https://arxiv.org/pdf/2404.10518

In [ ]:
import timm

### mobilenetv4_conv_medium 8.5M 91.35

In [ ]:
model_name = "hf_hub:timm/mobilenetv4_conv_medium.e500_r256_in1k"
model = timm.create_model(model_name, pretrained=True)
model.classifier =  nn.Sequential(
          nn.Linear(in_features=1280, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/679 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/39.2M [00:00<?, ?B/s]

Number of parameters: 8516756


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

...

Epoch 3) train acc: 90.06, val acc: 91.34


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 91.25, val acc: 90.39


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 92.51, val acc: 90.52


### mobilenetv4_conv_small 2.5M 90.99

In [ ]:
model_name = "hf_hub:timm/mobilenetv4_conv_small.e2400_r224_in1k"
model = timm.create_model(model_name, pretrained=True)
model.classifier =  nn.Sequential(
          nn.Linear(in_features=1280, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

config.json:   0%|          | 0.00/681 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/15.2M [00:00<?, ?B/s]

Number of parameters: 2575268


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 88.8, val acc: 90.99


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 91.15, val acc: 90.87


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 91.92, val acc: 88.44


## Try Segmentation Masks

In [ ]:
# x_train = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_train.pt")
masks_train = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/masks_train.pt")
# y_train = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_train.pt")
# x_val = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_val.pt")
masks_val = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/masks_train.pt")
# y_val = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_val.pt")

In [ ]:
class MyDataset2(Dataset):
    def __init__(self, data, masks, target, transform=None, target_transform=None):
        self.data = data
        self.masks = masks
        self.target = target
        self.transform = transform
        self.target_transform = target_transform

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        x = self.data[index]
        if self.transform:
            x = self.transform(x)
        x = x * self.masks[index]

        y = self.target[index]
        if self.target_transform:
            y = self.target_transform(y)

        return x, y

In [ ]:
df_train = MyDataset2(x_train, masks_train, y_train.long())
df_val = MyDataset2(x_val, masks_val, y_val.long())

image_size = (256, 256)
train_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 84.66, val acc: 75.23


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.42, val acc: 81.98


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.71, val acc: 84.22


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.67, val acc: 83.54


In [ ]:
class MyDataset3(Dataset):
    def __init__(self, data, masks, target, transform=None, target_transform=None):
        self.data = data
        self.masks = masks
        self.target = target
        self.transform = transform
        self.target_transform = target_transform

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        x = self.data[index]
        if self.transform:
            x = self.transform(x)
        x = torch.cat((x, x * self.masks[index], self.masks[index]), 1)

        y = self.target[index]
        if self.target_transform:
            y = self.target_transform(y)

        return x, y

In [ ]:
df_train = MyDataset3(x_train, masks_train, y_train.long())
df_val = MyDataset3(x_val, masks_val, y_val.long())

image_size = (256, 256)
train_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.RandomHorizontalFlip(p=0.5),
    # v2.RandomRotation(degrees=20),
    # v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    # v2.RandomAffine(degrees=15, translate=(0.1, 0.1), scale=(0.9, 1.1), shear=10),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize([0.507], [0.253])
])

# Only normalization and resizing for validation set
val_transforms = v2.Compose([
    v2.Resize(image_size),
    # v2.ToTensor(),
    # v2.ToDtype(torch.float32),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.67, val acc: 88.23


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 94.82, val acc: 91.68


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.26, val acc: 87.36


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 96.03, val acc: 91.15


## Augmentations

### ColorJitter

In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Downloading: "https://download.pytorch.org/models/regnet_y_3_2gf-9180c971.pth" to /root/.cache/torch/hub/checkpoints/regnet_y_3_2gf-9180c971.pth
100%|██████████| 74.6M/74.6M [00:00<00:00, 178MB/s]


Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.32, val acc: 93.64


...

Epoch 3) train acc: 93.57, val acc: 94.24


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.44, val acc: 89.26


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.44, val acc: 91.94


In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Downloading: "https://download.pytorch.org/models/regnet_y_3_2gf-9180c971.pth" to /root/.cache/torch/hub/checkpoints/regnet_y_3_2gf-9180c971.pth
100%|██████████| 74.6M/74.6M [00:01<00:00, 72.2MB/s]


Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.47, val acc: 90.93


...

Epoch 3) train acc: 93.79, val acc: 92.16


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.84, val acc: 93.17


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.28, val acc: 89.54


In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(brightness=0.4, contrast=0.4, saturation=0.4),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.76, val acc: 90.43


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.28, val acc: 92.79


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.21, val acc: 93.32


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.8, val acc: 93.95


In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(brightness=0.3, contrast=0.3),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Downloading: "https://download.pytorch.org/models/regnet_y_3_2gf-9180c971.pth" to /root/.cache/torch/hub/checkpoints/regnet_y_3_2gf-9180c971.pth
100%|██████████| 74.6M/74.6M [00:05<00:00, 13.5MB/s]


Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.61, val acc: 93.64


...

Epoch 3) train acc: 93.11, val acc: 93.45


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.4, val acc: 93.04


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.1, val acc: 94.71


In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(contrast=0.3, saturation=0.3),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Downloading: "https://download.pytorch.org/models/regnet_y_3_2gf-9180c971.pth" to /root/.cache/torch/hub/checkpoints/regnet_y_3_2gf-9180c971.pth
100%|██████████| 74.6M/74.6M [00:01<00:00, 71.6MB/s]


Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.39, val acc: 92.76


...

Epoch 3) train acc: 93.93, val acc: 93.01


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.74, val acc: 93.54


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.65, val acc: 93.57


In [ ]:
train_transforms = v2.Compose([
    v2.ColorJitter(brightness=0.3, saturation=0.3),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.34, val acc: 81.01


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.92, val acc: 91.46


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.43, val acc: 91.56


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.31, val acc: 93.45


### RandomHorizontalFlip

In [ ]:
train_transforms = v2.Compose([
    v2.RandomHorizontalFlip(p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.13, val acc: 91.91


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 3) train acc: 93.06, val acc: 91.56


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 93.61, val acc: 91.59


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.48, val acc: 94.14


### CenterCrop

In [ ]:
train_transforms = v2.Compose([
    v2.CenterCrop(256),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.CenterCrop(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.04, val acc: 91.34


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.89, val acc: 94.54


...

Epoch 3) train acc: 94.22, val acc: 95.2


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.13, val acc: 93.03


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.63, val acc: 94.89


In [ ]:
train_transforms = v2.Compose([
    v2.CenterCrop(224),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.CenterCrop(224),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.78, val acc: 88.82


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 91.64, val acc: 90.39


...

Epoch 3) train acc: 93.31, val acc: 89.2


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.28, val acc: 91.97


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.35, val acc: 90.27


In [ ]:
train_transforms = v2.Compose([
    v2.CenterCrop(192),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.CenterCrop(192),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 85.45, val acc: 92.09


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 90.66, val acc: 91.24


...

Epoch 3) train acc: 92.84, val acc: 91.72


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.21, val acc: 91.75


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 94.9, val acc: 90.93


In [ ]:
train_transforms = v2.Compose([
    v2.CenterCrop(272),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.CenterCrop(272),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.11, val acc: 92.91


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.92, val acc: 92.03


...

Epoch 3) train acc: 94.28, val acc: 91.87


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.75, val acc: 93.89


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.8, val acc: 93.04


### Resize

In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.71, val acc: 88.79


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.22, val acc: 93.35


...

Epoch 3) train acc: 93.77, val acc: 92.72


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.7, val acc: 92.94


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.93, val acc: 94.2


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(224),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(224),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.9, val acc: 92.44


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.39, val acc: 92.76


...

Epoch 3) train acc: 94.15, val acc: 93.42


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.13, val acc: 92.09


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.77, val acc: 93.76


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(192),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(192),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.69, val acc: 92.0


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.26, val acc: 93.54


...

Epoch 3) train acc: 94.13, val acc: 94.46


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.77, val acc: 93.01


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.8, val acc: 91.94


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(272),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(272),
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.98, val acc: 91.09


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.59, val acc: 89.35


...

Epoch 3) train acc: 94.02, val acc: 91.62


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.71, val acc: 93.32


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.46, val acc: 93.35


### RandomResizedCrop

In [ ]:
train_transforms = v2.Compose([
    v2.RandomResizedCrop(size=256, scale=(0.6, 1)),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 84.1, val acc: 88.44


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 89.4, val acc: 91.97


...

Epoch 3) train acc: 91.11, val acc: 93.76


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 91.85, val acc: 90.08


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 92.25, val acc: 93.23


### RandomAdjustSharpness

In [ ]:
train_transforms = v2.Compose([
    v2.RandomAdjustSharpness(sharpness_factor=2, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.32, val acc: 93.1


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.91, val acc: 92.6


...

Epoch 3) train acc: 93.71, val acc: 94.33


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.88, val acc: 93.61


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.82, val acc: 92.31


In [ ]:
train_transforms = v2.Compose([
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.09, val acc: 92.76


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.55, val acc: 93.61


...

Epoch 3) train acc: 93.65, val acc: 96.36


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.82, val acc: 92.57


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.48, val acc: 95.36


In [ ]:
train_transforms = v2.Compose([
    v2.RandomAdjustSharpness(sharpness_factor=1.3, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.1, val acc: 93.01


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.51, val acc: 91.62


...

Epoch 3) train acc: 94.02, val acc: 93.64


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.04, val acc: 94.14


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.4, val acc: 93.64


In [ ]:
train_transforms = v2.Compose([
    v2.RandomAdjustSharpness(sharpness_factor=1.7, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.63, val acc: 90.02


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.72, val acc: 92.44


...

Epoch 3) train acc: 93.76, val acc: 94.49


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 94.82, val acc: 91.84


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.86, val acc: 94.65


### RandomAutocontrast

In [ ]:
train_transforms = v2.Compose([
    v2.RandomAutocontrast(p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])

df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 5
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.9, val acc: 89.35


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 92.5, val acc: 93.64


...

Epoch 3) train acc: 93.91, val acc: 93.76


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 4) train acc: 95.04, val acc: 92.47


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 5) train acc: 95.55, val acc: 92.13


## Multiple Augmentations

### 4 at once

In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.28, val acc: 92.44


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.35, val acc: 93.95


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 94.53, val acc: 93.95


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.03, val acc: 91.43


### 3 at once

In [ ]:
train_transforms = v2.Compose([
    v2.RandomHorizontalFlip(p=0.5),
    v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.33, val acc: 92.09


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.16, val acc: 91.62


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 94.35, val acc: 94.02


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.08, val acc: 90.74


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.02, val acc: 91.15


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 95.34, val acc: 92.5


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 96.01, val acc: 93.26


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 96.37, val acc: 93.61


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.11, val acc: 92.09


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.57, val acc: 93.5


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 94.73, val acc: 96.21


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.44, val acc: 94.32


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 86.84, val acc: 89.54


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.03, val acc: 93.7


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 94.38, val acc: 92.22


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.11, val acc: 89.04


### 2 at once

In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.84, val acc: 89.42


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 95.84, val acc: 93.89


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 96.29, val acc: 93.86


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 97.04, val acc: 93.54


In [ ]:
train_transforms = v2.Compose([
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.47, val acc: 87.56


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.67, val acc: 94.24


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 95.19, val acc: 93.42


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.34, val acc: 94.93


In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Number of parameters: 18020430


Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 87.33, val acc: 85.73


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 5) train acc: 94.67, val acc: 92.25


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 94.95, val acc: 93.76


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 95.45, val acc: 94.36


## Freeze test

In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 16
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)
print('Number of parameters:', sum(p.numel() for p in model.parameters()))

Number of parameters: 18020430


In [ ]:
print('Number of parameters:', sum(p.numel() for p in model.stem.parameters()))
print('Number of parameters:', sum(p.numel() for p in model.trunk_output.block1.parameters()))
print('Number of parameters:', sum(p.numel() for p in model.trunk_output.block2.parameters()))
print('Number of parameters:', sum(p.numel() for p in model.trunk_output.block3.parameters()))
print('Number of parameters:', sum(p.numel() for p in model.trunk_output.block4.parameters()))
print('Number of parameters:', sum(p.numel() for p in model.fc.parameters()))

Number of parameters: 928
Number of parameters: 56186
Number of parameters: 793602
Number of parameters: 12268854
Number of parameters: 4803768
Number of parameters: 97092


In [ ]:
i = 0
while True:
    try:
        print('Number of parameters:', sum(p.numel() for p in model.trunk_output.block3[i].parameters()))
        i += 1
    except:
        break

Number of parameters: 772470
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032
Number of parameters: 958032


### Freeze 57k

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.67, val acc: 92.39


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 93.3, val acc: 94.87


...

Epoch 5) train acc: 96.4, val acc: 95.1


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 96.95, val acc: 91.16


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 97.52, val acc: 93.87


### Freeze 850k

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(3):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.71, val acc: 93.48


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 93.66, val acc: 91.5


...

Epoch 5) train acc: 96.42, val acc: 96.81


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 97.25, val acc: 95.94


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 97.31, val acc: 93.64


### Freeze 3.5m

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(3):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 1) train acc: 89.9, val acc: 94.91


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 2) train acc: 94.34, val acc: 95.03


...

Epoch 5) train acc: 96.75, val acc: 96.26


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 6) train acc: 97.13, val acc: 95.06


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 7) train acc: 97.73, val acc: 96.17


### Freeze 6.4m

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(6):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.32, val acc: 93.17


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 93.72, val acc: 95.29


...

Epoch 5) train acc: 96.87, val acc: 97.13


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 97.54, val acc: 94.79


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 97.91, val acc: 95.04


### Freeze 9.3m

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(9):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 88.92, val acc: 95.39


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 94.39, val acc: 93.78


...

Epoch 5) train acc: 97.95, val acc: 94.91


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 98.18, val acc: 91.91


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 98.52, val acc: 94.73


### Freeze 13.1m

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for param in model.trunk_output.block3.parameters():
    param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 7
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 89.04, val acc: 93.8


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 2) train acc: 94.47, val acc: 95.26


...

Epoch 5) train acc: 97.94, val acc: 95.36


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 6) train acc: 98.2, val acc: 95.54


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 7) train acc: 98.62, val acc: 95.64


## Final

In [ ]:
train_transforms = v2.Compose([
    v2.Resize(256),
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomAdjustSharpness(sharpness_factor=1.5, p=0.5),
    v2.Normalize([0.507], [0.253])
])
val_transforms = v2.Compose([
    v2.Resize(256),
    v2.Normalize(mean=[0.507], std=[0.253])
])
df_train.transform = train_transforms
df_val.transform = val_transforms

batch_size = 32
train_loader = DataLoader(df_train, batch_size=batch_size, shuffle=False)
val_loader = DataLoader(df_val, batch_size=batch_size, shuffle=False)

In [ ]:
x_test = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/x_test.pt")
y_test = torch.load("/content/drive/MyDrive/COVID-19_Radiography_Dataset/df/y_test.pt")
df_test = MyDataset(x_test, y_test.long())
df_test.transform = val_transforms
test_loader = DataLoader(df_test, batch_size=batch_size, shuffle=False)

In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(3):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
epochs = 15
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=None, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 1) train acc: 89.91, val acc: 94.42


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 2) train acc: 94.13, val acc: 93.71


...

Epoch 13) train acc: 98.71, val acc: 93.81


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 14) train acc: 99.03, val acc: 97.0


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 15) train acc: 99.1, val acc: 93.06


In [ ]:
model = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
model.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
model.to(device)

for param in model.parameters():
    param.requires_grad = True
for param in model.stem.parameters():
    param.requires_grad = False
for param in model.trunk_output.block1.parameters():
    param.requires_grad = False
for param in model.trunk_output.block2.parameters():
    param.requires_grad = False
for i in range(3):
    for param in model.trunk_output.block3[i].parameters():
        param.requires_grad = False

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(model.parameters())
scheduler = lr_scheduler.MultiStepLR(optimizer, milestones=[7, 9], gamma=0.1)
epochs = 11
hist = train_val(model=model, optimizer=optimizer, criterion=criterion, scheduler=scheduler, epochs=epochs,
          train_loader=train_loader, val_loader=val_loader, train_size=len(df_train), val_size=len(df_val))

Epoch::   0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 1) train acc: 90.0, val acc: 94.77


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 2) train acc: 94.08, val acc: 94.99


...

Epoch 9) train acc: 99.2, val acc: 97.21


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 10) train acc: 99.49, val acc: 97.21


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 11) train acc: 99.58, val acc: 96.88


In [3]:
test(model=model, criterion=criterion, test_loader=test_loader, test_size=len(df_test))

Test acc: 97.16


In [ ]:
torch.save(student.cpu().state_dict(), 'model_small_scripted.pt')

## Knowledge distillation

In [ ]:
def train_val_knowledge_distillation(teacher, student, optimizer, criterion, scheduler, epochs, train_loader, val_loader,
                                 train_size, val_size, T, soft_target_loss_weight):
    history = []
    ce_loss_weight = 1 - soft_target_loss_weight
    pbar = trange(epochs, desc="Epoch:")
    for epoch in pbar:
        train_correct = 0
        val_correct = 0
        teacher.eval()  # Teacher set to evaluation mode
        student.train() # Student to train mode
        for inputs, targets in tqdm(train_loader):
            optimizer.zero_grad()
            with torch.autocast(device_type="cuda", dtype=torch.float16):
                with torch.no_grad():
                    teacher_logits = teacher(inputs.to(device).expand(-1,3,-1,-1))
                student_logits = student(inputs.to(device).expand(-1,3,-1,-1))

            #Soften the student logits by applying softmax first and log() second
            soft_targets = nn.functional.softmax(teacher_logits / T, dim=-1)
            soft_prob = nn.functional.log_softmax(student_logits / T, dim=-1)

            # Calculate the soft targets loss. Scaled by T**2 as suggested by the authors of the paper "Distilling the knowledge in a neural network"
            soft_targets_loss = -torch.sum(soft_targets * soft_prob) / soft_prob.size()[0] * (T**2)

            # Calculate the true label loss
            targets = targets.to(device) ##.squeeze().long()
            target_loss = criterion(student_logits, targets)

            # Weighted sum of the two losses
            loss = soft_target_loss_weight * soft_targets_loss + ce_loss_weight * target_loss

            loss.backward()
            optimizer.step()
            preds = torch.argmax(student_logits, 1)
            train_correct +=  torch.sum(preds == targets).item()
        train_acc = train_correct / train_size
        if scheduler:
            scheduler.step()

        student.eval()
        with torch.no_grad():
            for inputs, targets in val_loader:
                with torch.autocast(device_type="cuda", dtype=torch.float16):
                    if inputs.shape[1] == 1:
                        outputs = student(inputs.to(device).expand(-1,3,-1,-1))
                    else:
                        outputs = student(inputs.to(device))

                targets = targets.to(device) ##.squeeze().long()
                preds = torch.argmax(outputs, 1)
                val_correct +=  torch.sum(preds == targets).item()
        val_acc = val_correct / val_size
        print(f'Epoch {epoch + 1}) train acc: {round(100 * train_acc, 2)}, val acc: {round(100 * val_acc, 2)}')
        history.append((round(100 * train_acc, 2), round(100 * val_acc, 2)))
    return history

In [ ]:
teacher = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
teacher.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
teacher.load_state_dict(torch.load('model_scripted.pt',map_location=torch.device('cpu')))
teacher.to(device)

student = models.mobilenet_v3_large(weights='IMAGENET1K_V2')
student.classifier =  nn.Sequential(
          nn.Linear(in_features=960, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
student.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(student.parameters())
scheduler = None
epochs = 12
hist = train_val_knowledge_distillation(teacher=teacher, student=student, optimizer=optimizer, criterion=criterion,
                                        scheduler=scheduler, epochs=epochs, train_loader=train_loader, val_loader=val_loader,
                                        train_size=len(df_train), val_size=len(df_val), T=2, soft_target_loss_weight=0.35)

Downloading: "https://download.pytorch.org/models/mobilenet_v3_large-5c1a4163.pth" to /root/.cache/torch/hub/checkpoints/mobilenet_v3_large-5c1a4163.pth
100%|██████████| 21.1M/21.1M [00:00<00:00, 177MB/s]


Epoch::   0%|          | 0/12 [00:00<?, ?it/s]

  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 1) train acc: 89.64, val acc: 90.77


  0%|          | 0/926 [00:00<?, ?it/s]

...

Epoch 10) train acc: 98.21, val acc: 90.17


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 11) train acc: 97.98, val acc: 93.99


  0%|          | 0/926 [00:00<?, ?it/s]

Epoch 12) train acc: 98.82, val acc: 88.97


In [ ]:
teacher = models.regnet_y_3_2gf(weights='IMAGENET1K_V2')
teacher.fc =  nn.Sequential(
          nn.Linear(in_features=1512, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
teacher.load_state_dict(torch.load('model_scripted.pt',map_location=torch.device('cpu')))
teacher.to(device)

student = models.mobilenet_v3_large(weights='IMAGENET1K_V2')
student.classifier =  nn.Sequential(
          nn.Linear(in_features=960, out_features=64, bias=True),
          nn.ReLU(),
          nn.Linear(in_features=64, out_features=4, bias=True),
        )
student.to(device)

criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(student.parameters())
scheduler = lr_scheduler.MultiStepLR(optimizer, milestones=[6, 8], gamma=0.1)
epochs = 9
hist = train_val_knowledge_distillation(teacher=teacher, student=student, optimizer=optimizer, criterion=criterion,
                                        scheduler=scheduler, epochs=epochs, train_loader=train_loader, val_loader=val_loader,
                                        train_size=len(df_train), val_size=len(df_val), T=2, soft_target_loss_weight=0.35)

Epoch::   0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 1) train acc: 90.15, val acc: 93.66


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 2) train acc: 94.15, val acc: 91.49


...

Epoch 7) train acc: 98.12, val acc: 96.48


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 8) train acc: 98.6, val acc: 96.57


  0%|          | 0/463 [00:00<?, ?it/s]

Epoch 9) train acc: 98.99, val acc: 96.50


In [4]:
test(model=student, criterion=criterion, test_loader=test_loader, test_size=len(df_test))

Test acc: 96.24


## End